# Recommendation Engines: Implementing Surprise
- Surprise is a scikit library that stands for **Simple Python RecommendatIon System Engine**
- Has built-in similarity metrics, baseline methods, content-based systems, matrix factorization systems

In this notebook, we'll first walk through setting up a super basic recommendation system, using the popular MovieLens 100K Dataset. Then, we'll look into more detail how Surprise works.

## Fitting and Predicting with Surprise

### 1. Install surprise if you haven't, and import the usual libraries.

In [1]:
# !pip install surprise

In [3]:
# import libraries
import numpy as np
import pandas as pd

from surprise import Dataset, Reader
from surprise import SVD
from surprise import accuracy
from surprise.model_selection import cross_validate, train_test_split

### 2. Load in the dataset

Surprise has the dataset built in. You might need to download the dataset so follow the instructions in the code output! Unfortunately, the Surprise data format doesn't let us inspect the data, but here is the documentation: https://grouplens.org/datasets/movielens/100k/


In [4]:
data = Dataset.load_builtin('ml-100k')

# train-test split
train, test = train_test_split(data, test_size=.2)

In [5]:
train?

In [6]:
train.ur

defaultdict(list,
            {0: [(0, 5.0),
              (10, 5.0),
              (338, 4.0),
              (88, 3.0),
              (106, 3.0),
              (172, 5.0),
              (904, 4.0),
              (149, 2.0),
              (485, 3.0),
              (153, 5.0),
              (466, 4.0),
              (216, 4.0),
              (274, 4.0),
              (503, 3.0),
              (809, 4.0),
              (345, 4.0),
              (123, 5.0),
              (997, 2.0),
              (1217, 5.0),
              (203, 3.0),
              (208, 3.0),
              (588, 4.0),
              (610, 3.0),
              (695, 3.0),
              (482, 4.0),
              (104, 4.0),
              (64, 5.0),
              (638, 4.0),
              (239, 4.0),
              (454, 2.0),
              (568, 4.0),
              (374, 4.0),
              (176, 4.0),
              (676, 4.0),
              (729, 3.0),
              (109, 5.0),
              (204, 3.0),
              (93, 4.

In [7]:
train.ir

defaultdict(list,
            {0: [(0, 5.0),
              (49, 4.0),
              (200, 4.0),
              (172, 4.0),
              (119, 5.0),
              (48, 4.0),
              (337, 5.0),
              (638, 3.0),
              (195, 5.0),
              (100, 4.0),
              (672, 4.0),
              (455, 5.0),
              (87, 4.0),
              (114, 3.0),
              (238, 4.0),
              (80, 5.0),
              (879, 3.0),
              (56, 3.0),
              (538, 3.0),
              (102, 3.0),
              (130, 4.0),
              (457, 4.0),
              (116, 5.0),
              (139, 3.0),
              (267, 5.0),
              (33, 4.0),
              (163, 4.0),
              (450, 4.0),
              (427, 2.0),
              (373, 5.0),
              (155, 5.0),
              (605, 4.0),
              (347, 5.0),
              (428, 4.0),
              (378, 3.0),
              (308, 5.0),
              (192, 3.0),
              (199, 3.0),

### 3. Run the default Singular Value Decomposition Model!

In [8]:
svd = SVD()
svd.fit(train)
predictions = svd.test(test)

In [9]:
prediction = predictions[0]
prediction?

In [13]:
prediction?

In [11]:
accuracy.rmse(predictions)

RMSE: 0.9448


0.9447803224753457

### 4. Make a prediction!

In [14]:
uid = str(196)  # raw user id (as in the ratings file). They are **strings**!
iid = str(302)

# get a prediction for specific users and items.
pred = svd.predict(uid, iid, r_ui=4, verbose=True)

user: 196        item: 302        r_ui = None   est = 3.91   {'was_impossible': False}


## Applying Surprise

### 1. How does Surprise take in your data?
https://surprise.readthedocs.io/en/stable/getting_started.html#use-a-custom-dataset

The dataset we'll use is a subset of the Yelp Open Dataset that's already been joined and cleaned.
https://www.yelp.com/dataset

In [15]:
yelp = pd.read_csv('yelp_reviews.csv').drop(['Unnamed: 0'], axis = 1)

In [16]:
yelp.head()

user_id             business_id  stars
0  brd33PD_6nqK_VVnO3NWAg  --1UhMGODdWsrMastO9DZw    4.0
1  NqpKiaRsGfuU2voV5dPRCQ  --1UhMGODdWsrMastO9DZw    1.0
2  dhzlnpisqA7V1zfiO12AZA  --1UhMGODdWsrMastO9DZw    2.0
3  A4bpHuvzaQt9-XAg8e9Msw  --1UhMGODdWsrMastO9DZw    3.0
4  GL81ktDIteXA2VVH6gIakg  --1UhMGODdWsrMastO9DZw    5.0

### 2. Inspecting the dataset:

Here's where you'd do a **comprehensive** EDA!

In [17]:
yelp.shape

(100000, 3)

In [18]:
print('Number of Users: ', len(yelp['user_id'].unique()))
print('Number of Businesses: ', len(yelp['business_id'].unique()))

Number of Users:  79773
Number of Businesses:  2518


1. What's the distribution of ratings? i.e. How many 1-star, 2-star, 3-star reviews?
2. How many reviews does a restaurant have?
3. How many reviews does a user make?

In [19]:
yelp['stars'].value_counts()

5.0    42685
4.0    23143
1.0    14315
3.0    11522
2.0     8335
Name: stars, dtype: int64

In [20]:
yelp['business_id'].value_counts()

-ed0Yc9on37RoIoG2ZgxBA    1694
--9e1ONYQuAa-CB_Rrw7Tw    1661
-6tvduBzjLI1ISfs3F_qTg    1194
-U7tvCtaraTQ9b0zBhpBMA    1180
-FLnsWAa4AGEW4NgE8Fqew    1128
                          ... 
-ApqBP-q8OXWKJ-B6zPaPg       3
-We079O7Dij5v86ZOBALfQ       3
-FWhwGTP9YsV_5ONgdQ4hg       3
-E4-EuyTr1G5Y_klky8cZQ       3
-9Tfvyk5ip565mhYBs0zMQ       3
Name: business_id, Length: 2518, dtype: int64

In [21]:
yelp['user_id'].value_counts()

CxDOIDnH8gp9KXzpBHJYXw    50
U4INQZOPSUaj8hMjLlZ3KA    33
bLbSNkLggFnqwNNzzq-Ijw    31
QJI9OSEn6ujRCtrX06vs1w    27
DK57YibC5ShBmqQl97CKog    27
                          ..
TpdUmfRh_WGZUHksC2LTpw     1
M8DD9IIyq_NpI-A9K_Vfaw     1
M0GqHIj8EWZGDe5TDQao2Q     1
8fxlHzFsLp5vymxkf8TNPA     1
cnLljmhzrjgv_yQ8xs-PQQ     1
Name: user_id, Length: 79773, dtype: int64

### 3. Reading in the dataset and prepping data

In [22]:
# Instantiate a 'Reader' to read in the data so Surprise can use it
reader = Reader(rating_scale=(1, 5))

# The columns must correspond to user id, item id and ratings (in that order).
data = Dataset.load_from_df(yelp[['user_id', 'business_id', 'stars']], reader)

In [23]:
type(data)

surprise.dataset.DatasetAutoFolds

In [24]:
trainset, testset = train_test_split(data, test_size=.2)

In [25]:
trainset

### 4. Fitting and evaluating models
Here, let's assume that we've tuned all these hyperparameters using GridSearch, and we've arrived at our final model.

In [27]:
final = SVD(n_epochs=20, n_factors=1, biased=True, 
              lr_all=0.005, reg_all=0.06)

In [28]:
final.fit(trainset)

In [29]:
predictions = final.test(testset)

In [30]:
predictions[:3]

[Prediction(uid='cT_rZW640dxWY8gzNu6xQQ', iid='-8R_-EkGpUhBk55K9Dd4mg', r_ui=5.0, est=3.699846444224332, details={'was_impossible': False}),
 Prediction(uid='qCoSEv7KNy5mMp_33Z-Gkw', iid='-ed0Yc9on37RoIoG2ZgxBA', r_ui=2.0, est=4.123449452275196, details={'was_impossible': False}),
 Prediction(uid='VP_wcmHhC1BTcEKoVUXX8A', iid='-YYhUIdX-oJoqwd47sAJSw', r_ui=5.0, est=4.3089335813869045, details={'was_impossible': False})]

In [32]:
accuracy.rmse(predictions)
accuracy.mae(predictions)

RMSE: 1.3065
MAE:  1.0590


1.058991993469868

### 5. Making Predictions (again)
Unfortunately, this dataset has a convoluted string as the user/business IDs.

In [33]:
yelp['user_id'][55]

'HPtjvIrhzAUkKsiVkeT4MA'

In [34]:
yelp['business_id'][123]

'--7zmmkVg-IMGaXbuVd0SQ'

In [35]:
final.predict(yelp['user_id'][55], yelp['business_id'][13])

Prediction(uid='HPtjvIrhzAUkKsiVkeT4MA', iid='--1UhMGODdWsrMastO9DZw', r_ui=None, est=4.045184874870598, details={'was_impossible': False})

### 6. What else?

Surprise has sample code where you can get the top **n** recommended items for a user. https://surprise.readthedocs.io/en/stable/FAQ.html

# Resources

- The structure of our lesson on recommendation engines is based on Chapter 9 of **Mining of Massive Datasets**: http://infolab.stanford.edu/~ullman/mmds/book.pdf
- Libraries for coding recommendation engines: 
    - Surprise: https://surprise.readthedocs.io/en/stable/index.html
    - LightFM: https://lyst.github.io/lightfm/docs/index.html
    
    
- Some blogs I might've written:
    - Overview: https://towardsdatascience.com/a-primer-to-recommendation-engines-49bd12ed849f?source=friends_link&sk=279dfeec5187614b37431dab167fd4e3
    - Collaborative filtering: https://towardsdatascience.com/a-primer-to-recommendation-engines-49bd12ed849f?source=friends_link&sk=279dfeec5187614b37431dab167fd4e3